In [310]:
# python -m pip install --index-url=https://bcms.bloomberg.com/pip/simple blpapi
# python -m pip install xbbg
# python -m pip install numpy
# python -m pip install scikit-learn

from xbbg import blp
import numpy as np
from sklearn.linear_model import LinearRegression
import math

In [311]:
class Time_Series:
    
    def __init__(self, s1, s2, start, end, fld='TOT_RETURN_INDEX_GROSS_DVDS'):
        self._s1 = s1
        self._s2 = s2
        self._fld= fld

        self._df = blp.bdh(tickers=[self._s1, self._s2], flds=self._fld, start_date=start, end_date=end,)
        
        self._df.columns = [self._s1, self._s2]
        self._df = self._df.dropna()
        
        self._df['r1'] = np.log(self._df[self._s1] / self._df[self._s1].shift(1))
        self._df['r2'] = np.log(self._df[self._s2] / self._df[self._s2].shift(1))
        
        self._df = self._df.dropna()
        
        c = self._df.columns.tolist()
        c = [c[0], c[2], c[1], c[3]]
        self._df = self._df[c]
        
        self._n = len(self._df)
        
        X = self._df['r2'].values.reshape(-1, 1)
        y = self._df['r1'].values
        model = LinearRegression().fit(X, y)
        self._ols_a   = model.intercept_
        self._ols_b   = model.coef_
        self._ols_rsq = model.score(X, y)        
        
        return None
    
    def df(self):
        return self._df
        
    def time_series_return(self, s):
        return np.mean(s)
    
    def time_series_std_dev(self, s):
        return np.std(s)
    
    def annualized_return(self, s):
        return np.mean(s) * 252
    
    def annualized_std_dev(self, s):
        return np.std(s) * math.sqrt(252)
    
    def analysis(self, analysis_type='e'):
        
        t = list(analysis_type)[0].lower()
        
        d = {
            'e' : self._df['r1'],
            'b' : self._df['r2'],
            'a' : self._df['r1'] - self._df['r2'],
        }
        
        s = d.get(t, self._df['r1'])
        
        r_ts = self.time_series_return(s)
        r_an = self.annualized_return(s)
        
        sd_ts = self.time_series_std_dev(s)
        sd_an = self.annualized_std_dev(s)
        
        a = {
            'e' : self._s1,
            'b' : self._s2,
            'a' : 'Active',
        }
        
        print(a.get(t, self._s1) + ' Analysis:')
        print("%30s %15s" % ('Time Series', 'Annualized'))
        print("Total return   %15.6f" % (r_ts * self._n))
        print("Num. obs.      %15d" % self._n)
        print("Mean return    %15.6f %15.6f" % (r_ts, r_an))
        print("Std Devn       %15.6f %15.6f" % (sd_ts, sd_an))
        print("Ratio          %15.6f %15.6f" % (r_ts/sd_ts, r_an/sd_an))
        if t == 'e':
            print("OLS Intercept  %15.6f" % self._ols_a)
            print("OLS Beta       %15.6f" % self._ols_b)
            print("OLS R-squared  %15.6f" % self._ols_rsq)
        
        return None
        
    def equity_analysis(self):
        return self.analysis('e')
    
    def benchmark_analysis(self):
        return self.analysis('e')
    
    def active_analysis(self):
        return self.analysis('a')
        

In [312]:
ts = Time_Series('JABAX US Equity', 'MSAAMMOR Index', '2020-12-31', '2021-06-30') # 'SOFRINDX Index'
ts.df().head()

JABAX US Equity        r1  MSAAMMOR Index        r2
2021-01-04            40.55 -0.010548        4220.494 -0.003589
2021-01-05            40.65  0.002463        4232.586  0.002861
2021-01-06            40.63 -0.000492        4251.219  0.004393
2021-01-07            40.99  0.008821        4274.727  0.005514
2021-01-08            41.11  0.002923        4289.767  0.003512

In [313]:
ts.analysis()

JABAX US Equity Analysis:
                   Time Series      Annualized
Total return          0.081506
Num. obs.                  124
Mean return           0.000657        0.165641
Std Devn              0.005933        0.094183
Ratio                 0.110788        1.758711
OLS Intercept         0.000001
OLS Beta              1.161297
OLS R-squared         0.715799


In [314]:
ts.analysis('b')

MSAAMMOR Index Analysis:
                   Time Series      Annualized
Total return          0.070063
Num. obs.                  124
Mean return           0.000565        0.142385
Std Devn              0.004322        0.068616
Ratio                 0.130719        2.075107


In [315]:
ts.active_analysis()

Active Analysis:
                   Time Series      Annualized
Total return          0.011443
Num. obs.                  124
Mean return           0.000092        0.023255
Std Devn              0.003239        0.051415
Ratio                 0.028493        0.452308


In [316]:
ts_rf = Time_Series('JABAX US Equity', 'SOFRINDX Index', '2020-12-31', '2021-06-30')
ts_rf.analysis('ACTV')

Active Analysis:
                   Time Series      Annualized
Total return          0.081362
Num. obs.                  124
Mean return           0.000656        0.165348
Std Devn              0.005933        0.094183
Ratio                 0.110593        1.755608
